In [1]:
#### 以下は使用しない ###
# distProb(state,act,dist,States): States中の状態s全てに対し(s,act)によりstateに遷移する確率を求める
# sの存在確率はdist[s]で、(s,act)によりstateに遷移する確率は moveProb(state,s,act)で与えられる
def distProb(state,act,dist,States,moveProb):
     return sum([moveProb(state, s, act)*dist[s] for s in States])

# g(state,act,ob,dist,States): 上記のdistProb(stte,act,dist,States)に観測確率 observationProb(ob,state)
# を掛けたもの --- Gに相当
def g(state,act,ob,dist,States,moveProb,observationProb):
     return observationProb(ob, state)*distProb(state,act,dist,States,moveProb)

# gTotal(act,ob,dist,States): States中の状態sすべてのGの値の総和
def gTotal(act,ob,dist,States,moveProb,observationProb):
    return sum([g(s,act,ob,dist,States,moveProb,observationProb) for s in States])

# f(state,act,ob,dist,States): actによってstateに遷移し観測obを得ることから計算される存在確率
def f(state,act,ob,dist,States,moveProb,observationProb):
    return g(state,act,ob,dist,States,moveProb,observationProb) / \
                gTotal(act,ob,dist,States,moveProb,observationProb)

# Statesの状態sすべての存在確率、一つ前の時点での存在確率dist, 行動actと観測obは与えられているとする
def allF(act,ob,dist,States, moveProb, observationProb):
    gAll=[observationProb(ob, state)*distProb(state,act,dist,States,moveProb) for state in States]
    # print(gAll)
    sumOfG = sum(gAll)
    return [x/sumOfG for x in gAll]


In [22]:
class Maze(object):
    def __init__(self, num, stateShape, dist=None, verbose=True):
        self.numOfRooms=num
        self.States=[i for i in range(num)]
        self.stateShape=stateShape
        self.verbose=verbose
        if dist != None:  # initial distribution
            self.StatesDist=dist
        else:  # uniform distribution
            self.StatesDist=[1.0/num for _ in range(num)]
    def update(self, action, observ, setting):
        self.StatesDist=setting.allF(action,observ,self.StatesDist,self.States)
        if self.verbose==True:
            print("\nThe new status:")
            self.formattedPrint(self.StatesDist)
    def formattedPrint(self,dist=None):
        if self.numOfRooms < 8:
            self.printLine(dist)
        else:
            self.showRooms(dist)
    def printLine(self, lst=None):
        if (lst == None):
            lst = self.StatesDist
        print("\t",end="")
        for x in lst:
            print(format(x,'.2f'),end="\t")
    def showRooms(self,dist=None):
        num=self.numOfRooms # num should be 10
        f = 0
        if dist==None:
            dist=self.StatesDist
        print("[")
        self.printLine(dist[f:f+4])
        print()
        self.printLine(dist[f+4:f+7])
        print()
        self.printLine(dist[f+7:])
        print("]")

In [10]:
# room shape & ob : 1 [upper],2 [right], 4[lower], 8 [left]
class Setting(object):
    def __init__(self, transitionProb, observationProb, maze):
        self.tranProb=transitionProb
        self.obsProb=observationProb
        self.shapes=maze.stateShape
        self.maze=maze
        self.actions=[self.possibleActions(s) for s in maze.stateShape]
    def possibleActions(self, room):
        actions=[]
        if (room % 2  == 0):
            actions +=['U']
        if ((room // 2) % 2 == 0):
            actions += ['R']
        if ((room //4) % 2 == 0):
            actions += ['D']
        if ((room // 8) % 2 == 0):
            actions += ['L']
        return actions
    def moveProb(self, newPos, oldPos, act):
        if (act == 'S'):  # stay
            if (newPos != oldPos):
                return 0.0
            else:
                return 1.0
        if (act not in self.actions[oldPos]):  # impossible move
            if (newPos == oldPos): # staying
                return 1.0
            else:
                return 0.0
        else:  # possible move
            if (newPos == oldPos):  #staying
                return 1-self.tranProb
            elif (act == 'R') and (newPos - oldPos == 1):
                return self.tranProb
            elif (act == 'L') and (oldPos - newPos == 1):
                return self.tranProb
            else:
                return 0.0
    def observationProb(self, observation, state):
        shape=self.shapes[state]
        if (observation == shape):
            return self.obsProb
        else:
            return (1.0 - self.obsProb)/15
    def distProb(self, state, act, dist, States):
            return sum([self.moveProb(state, s, act)*dist[s] for s in States])
    def allF(self,act,ob,dist,States):
        gAll=[self.observationProb(ob, state)*self.distProb(state,act,dist,States) for state in States]
        if self.maze.verbose==True:
            newdist = [self.distProb(state,act,dist,States) for state in States]
            print("Transition probability:")
            self.maze.formattedPrint(newdist)
            obsDist = [self.observationProb(ob, state) for state in States]
            print("\nObservation probability:")
            self.maze.formattedPrint(obsDist)
            print("\nG value:")
            self.maze.formattedPrint(gAll)
        sumOfG = sum(gAll)
        return [x/sumOfG for x in gAll]    
    

In [17]:
###### Sec.8.4 ########
print("Reidai --- Sec.8.4")
reidai=Maze(5,[13, 5, 5, 5, 7])   # ob : 5--- passage,  13 : left corner, 7: right corner
reidaiEnv=Setting(0.80, 0.70,reidai)

reidai.printLine()

Reidai --- Sec.8.4
	0.20	0.20	0.20	0.20	0.20	

In [18]:
print("\nMoving R and find it is a passage")
reidai.update('R',5,reidaiEnv) # moving right andd ob =5 (passage)


Moving R and find it is a passage
Transition probability:
	0.04	0.20	0.20	0.20	0.36	
Observation probability:
	0.02	0.70	0.70	0.70	0.02	
G value:
	0.00	0.14	0.14	0.14	0.01	
The new status:
	0.00	0.33	0.33	0.33	0.02	

In [19]:
# moving right and ob = 7 (right corner)
print("\nMoving R and find it is a right corner")
reidai.update('R',7,reidaiEnv)



Moving R and find it is a right corner
Transition probability:
	0.00	0.07	0.33	0.33	0.28	
Observation probability:
	0.02	0.02	0.02	0.02	0.70	
G value:
	0.00	0.00	0.01	0.01	0.19	
The new status:
	0.00	0.01	0.03	0.03	0.93	

In [20]:
# moving left and ob =5 (passage)
print("\nMoving L and find it is a passage")
reidai.update('L',5,reidaiEnv)



Moving L and find it is a passage
Transition probability:
	0.01	0.03	0.03	0.75	0.19	
Observation probability:
	0.02	0.70	0.70	0.70	0.02	
G value:
	0.00	0.02	0.02	0.53	0.00	
The new status:
	0.00	0.03	0.04	0.92	0.01	

In [25]:
### Exercise 8.2
print("\n\n  Exercise 8.2")
ex8_2=Maze(10,[9,1,1,7, 8,0,2, 12,4,6 ])     # ob : 1 [upper],2 [right], 4[lower], 8 [left]
ex8_2Env=Setting(0.80, 0.70, ex8_2)

ex8_2.showRooms()



  Exercise 8.2
[
	0.10	0.10	0.10	0.10	
	0.10	0.10	0.10	
	0.10	0.10	0.10	]


In [26]:
# stay  and ob = 2(right wall)
print("\nStay and find it has a wall on the right")
ex8_2.update('S',2,ex8_2Env)



Stay and find it has a wall on the right
Transition probability:
[
	0.10	0.10	0.10	0.10	
	0.10	0.10	0.10	
	0.10	0.10	0.10	]

Observation probability:
[
	0.02	0.02	0.02	0.02	
	0.02	0.02	0.70	
	0.02	0.02	0.02	]

G value:
[
	0.00	0.00	0.00	0.00	
	0.00	0.00	0.07	
	0.00	0.00	0.00	]

The new status:
[
	0.02	0.02	0.02	0.02	
	0.02	0.02	0.80	
	0.02	0.02	0.02	]


In [27]:
# moving left(2) and ob = 0 (no walls)
print("\nMoving Left and find it has no walls")
ex8_2.update('L',0,ex8_2Env)



Moving Left and find it has no walls
Transition probability:
[
	0.04	0.02	0.02	0.00	
	0.04	0.64	0.16	
	0.04	0.02	0.00	]

Observation probability:
[
	0.02	0.02	0.02	0.02	
	0.02	0.70	0.02	
	0.02	0.02	0.02	]

G value:
[
	0.00	0.00	0.00	0.00	
	0.00	0.45	0.00	
	0.00	0.00	0.00	]

The new status:
[
	0.00	0.00	0.00	0.00	
	0.00	0.98	0.01	
	0.00	0.00	0.00	]
